In [44]:
#Python 3.4.3
import re
import os
import collections
import time
import string
import math
from operator import itemgetter

#The project is divided in three parts:
#1. Making Index and getting exact top k retrieval
#2. Using the result of top k and comparing the result using inexact top k retrieving methods like: Champions List, 
#Index Elimination, Simple cluster pruning.
#3.Performance comparision.


class index:
    def __init__(self,path):
        #Initializing the values.
        self.path= path
        self.list1 = []
        self.od={}        
        self.master_dict = {}
        self.dict3 = {}
        self.doc_list = {}
        self.termFreqidf = {}
        
    #This function build the index by calculating the idf, id, wtf. While building the index, stop words are removed.
    #Query is converted into lower case and all the punctuations are removed.
    def buildIndex(self):
        start = time.time()
        docid = 1    
        #This is the list of characters which we want to remove from the index we create
        stoplistChar= ['a' ,'an' ,'and' ,'are' ,'as' ,'at' ,'be' ,'by' ,'for' ,'from' ,'has' ,'he' ,'in' ,'is' ,'it' ,'its' ,'of' ,'on' ,'that' ,'the' ,'to' ,'was' ,'were' ,'will' ,'with']
        #Collection of all the text files from the path given by the user
        for f in os.listdir(self.path):
            if f.endswith('.txt'):
                self.list1.append(f)
        #tokenization of all the files
        self.NumberOfDoc=len(self.list1)#Total number of documents
        for a in self.list1:
            pos = 1
            f = open(self.path+'/'+a)
            dict1 = {}
            for line in f:
                for word in line.split():
                    word = word.lower().translate(string.punctuation) #removes the string punctuation in the index
                     
                    if word in dict1:
                        dict1[word].append(pos)
                    elif word =='':
                        continue 
                    else:
                        dict1[word]=[pos]
                    pos+=1
            self.master_dict[docid]=[dict1]
            self.dict3[docid]=[a]
            self.doc_list[docid] = a  
            docid+=1
        dict2 = {}
        #making the index of the form : Term ID: [𝒊𝒅𝒇𝒕,(ID1,𝒘𝒕𝟏,𝒅𝟏, [pos1,pos2,..]), (ID2, 𝒘𝒕𝟐,𝒅𝟐, [pos1,pos2,…]),….]
        dict6 = {}
        counterr = 0
        for key, [value] in self.master_dict.items():
            for temp_key, temp_val in value.items():
                dict4 = {key: temp_val}
                if not temp_key in dict2:
                    dict2[temp_key]=[dict4]
                else:
                    dict2[temp_key].append(dict4)
        
        self.od = collections.OrderedDict(sorted(dict2.items()))

        for term in stoplistChar:
             del self.od[term] #To remove the term from our index
        #print(self.od)        
        for term in self.od.keys():
            self.termFreqidf[term]=[]
            doc_dictionary={}
            count = 0
            #calculating the inverted document frequency(idf) using the formula idf = log10(N/dft)
            for doc_dict in self.od[term]:
                count += 1  
            idf = math.log10((float) (self.NumberOfDoc) / count)
            self.termFreqidf[term].append(idf)
            for doc_dict in self.od[term]:
                for docs in doc_dict.keys():
                    tf = len(doc_dict[docs])
                    if tf == 0:
                        wtf = 0
                    else:
                        wtf = 1 + math.log10(tf)
                    wandplist=[]
                    wandplist.append(wtf)
                    wandplist.append(doc_dict[docs])
                    doc_dictionary[docs]=wandplist
            self.termFreqidf[term].append(doc_dictionary)
        end = time.time()
        print ('Retrieved in '+str(end-start) +' sec.')
    
    #retrieved time
    def print_dict(self):
        start = time.time()
        print ('indexes: ')
        print (self.termFreqidf)
        end = time.time()
        print ('Retrieved in '+str(end-start) +' sec.')
        
    #prints all the document list associated with the collection text files and print the retrieved time.
    def print_doc_list(self):
        start = time.time()
        print ('Doc List: ')
        for doc_id in self.doc_list:
            print ("Doc id: " + str(doc_id) + " => " + self.doc_list[doc_id])
        end = time.time()
        print ('Retrieved in '+str(end-start) +' sec.')
     
    #using the cosine similarity score taking the exact top k values in the reterieval process.
    def exact_query(self, query_terms, top_k,showResultTime):
        start = time.time()
        counter = 0 
        query= query_terms.split()
        query_tf = {}
        counterr=0
        dict_ve={}
        
        for term in query:
            if term in query_tf.keys():
                query_tf[term] += 1
            else:
                query_tf[term] =1
        query_tfidf={}
        ssumq = 0
        
        
        
        #using the q and v value to calculate the cosine scpre for the exact top k. 
        #q is the tf-idf weight of term i in the query.
        #d is the tf-idf weight of term i in the document.
        
        for term in query_tf.keys():
            q=1+ math.log10(query_tf[term])
            ssumq += q**2
            query_tfidf[term]= q
        cs_docs={}
        prod_sum={}
        ssumd={}
        for term in query_tfidf:
            if term in self.termFreqidf.keys():
                idf=self.termFreqidf[term][0]
                for docs in self.termFreqidf[term][1].keys():
                    tf=self.termFreqidf[term][1][docs][0]
                    tfidf_td = tf*idf
                    if docs in prod_sum.keys():
                        prod_sum[docs] += query_tfidf[term]*tfidf_td
                    else:
                        prod_sum[docs] = query_tfidf[term]*tfidf_td
                    if docs in ssumd.keys():
                        ssumd[docs] += (tfidf_td)**2
                    else:
                        ssumd[docs] = (tfidf_td)**2
            else:
                print (term + " not found in documents")
                #using the formula of cosine for calculating the cosine score.
        for docs in prod_sum.keys():
            cs_docs[docs]=( prod_sum[docs] / (math.sqrt(ssumd[docs])*math.sqrt(ssumq)) )
        cs_od = collections.OrderedDict(sorted(cs_docs.items()))
        print ('exact query result:')
        count = 0
        for docs,value in sorted(cs_od.items(), key= itemgetter(1), reverse= True):
                if count <=top_k:
                        print ('Doc id: ' + str(docs))
                count += 1
        end = time.time()
        if showResultTime:
            print ('Time it is taking is for exact top k '+str(end-start) +' sec.')
    
    #In index elimination, using only the half of the query terms sorted in decreasing order of idf value.
    def inexact_query_index_elimination( self, query_terms, top_k,showResultTime):
        #to calulate the total time of getting the output.
        start = time.time()
        query= query_terms.split()
        query_tf = {}
        for term in query:
                if term in query_tf.keys():
                        query_tf[term] += 1
                else:
                        query_tf[term] =1
        query_tfidf={}
        ssumq = 0
        sumss =  0
        for term in query_tf.keys():
                q=1+ math.log10(query_tf[term])
                ssumq += q**2
                query_tfidf[term]= q
        cs_docs={}
        prod_sum={}
        ssumd={}
        #taking the half of the total query terms and computing the top k.
        #top k will be selected from the selected documents.
        for term in query_tfidf:
                if term in self.termFreqidf.keys():
                        idf=self.termFreqidf[term][0]
                        for docs in self.termFreqidf[term][1].keys():
                                tf=self.termFreqidf[term][1][docs][0]
                                tfidf_td = tf*idf
                                if docs not in prod_sum.keys():
                                        prod_sum[docs] = query_tfidf[term]*tfidf_td
                                else:
                                        prod_sum[docs] += query_tfidf[term]*tfidf_td
                                if docs not in ssumd.keys():
                                        ssumd[docs] = (tfidf_td)**2
                                else:
                                        ssumd[docs] += (tfidf_td)**2
                else:
                        print (term + " term is not in the document")
        #considering documents for high-tdf query term.
        #considering documents containing many terms.
        for docs in prod_sum.keys():
                cs_docs[docs]=( prod_sum[docs] / (math.sqrt(ssumd[docs])*math.sqrt(ssumq)) )
        cs_od = collections.OrderedDict(sorted(cs_docs.items()))
        count = 0
        new_cs_od={}
        for docs in cs_od.keys():
                if  (len(cs_od) / 2) >count:
                        new_cs_od[docs] = cs_od[docs]
                        count += 1
        #top k are selected from the selected documents.
        print ('Index Elimination top k:')
        count = 0
        for docs,value in sorted(new_cs_od.items(), key= itemgetter(1), reverse= True):
            if count <=top_k:
                print ("Doc id: "  + str(docs))
            count += 1
        end = time.time()
        if showResultTime:
            print ('Time it is taking for index elimination is '+str(end-start) +' sec.')    
    #preprocessing the terms and the documents.
    #for each term, a list of r documents that is based on the weighted term frequency 𝒘𝒕,𝒅.
    def inexact_query_champion(self, query_terms,top_k,showResultTime ):
        start = time.time()
        champion={}
        champ= {}
        counterr = 0
        thresh = 20
        for term in self.termFreqidf.keys():
                champion[term]={}
                idf=self.termFreqidf[term][0]
                for docs in self.termFreqidf[term][1].keys():
                        tf=self.termFreqidf[term][1][docs][0]
                        tfidf_td = tf*idf
                        champion[term][docs]=tfidf_td
        
        champion_od={}
        for term in champion.keys():
            counter=0
            champion_od[term]={}
            for doc,tfidf_doc_term in sorted(champion[term].items(),key=  itemgetter(1), reverse = True):
                if  thresh >counter:
                    champion_od[term][doc]=tfidf_doc_term
                    counter += 1
        query= query_terms.split()
        query_tf = {}
        for term in query:
                if not term in query_tf.keys():
                        query_tf[term] = 1
                else:
                        query_tf[term] +=1
        query_tfidf={}
        ssumq = 0
        ssumm = 0
        for term in query_tf.keys():
                q=1+ math.log10(query_tf[term])
                ssumq += q**2
                query_tfidf[term]= q
        cs_docs={}
        prod_sum={}
        ssumd={}
        for term in query_tfidf:
                if term in champion_od.keys():
                        for docs in champion_od[term].keys():
                                if docs in prod_sum.keys():
                                        prod_sum[docs] += query_tfidf[term]*champion_od[term][docs]
                                else:
                                        prod_sum[docs] = query_tfidf[term]*champion_od[term][docs]
                                if docs in ssumd.keys():
                                        ssumd[docs] += (champion_od[term][docs])**2
                                else:
                                        ssumd[docs] = (champion_od[term][docs])**2
                else:
                        print (term + " Term is not in the list of documents")
        for docs in prod_sum.keys():
                cs_docs[docs]=( prod_sum[docs] / (math.sqrt(ssumd[docs])*math.sqrt(ssumq)) )
        cs_od = collections.OrderedDict(sorted(cs_docs.items()))
        count = 0
        counters=0
        dictq={}
        dictp = {}
        #calculate the value of top k from the value of r where r is the number of documents of heighest weight.
        print ('top k from champion list:')
        for docs,value in sorted(cs_od.items(), key= itemgetter(1), reverse= True):
                if count <=top_k:
                        print ('Doc id: ' + str(docs))
                count += 1
        end = time.time()
        if showResultTime:
            print ('Time it is taking for champion list is '+str(end-start) +' sec.')
    

    

#EXECUTION
obj = index('D:\Study\Sem-2\IR\Assignment 1\collection')
print("-----------------------------BUILDING INDEX---------------------------------------------")
obj.buildIndex()
print("-----------------------------Exact Top K query Result-----------------------------------")
showResultTime = True
obj.exact_query("soviet rainfall president grand crystal", 3,showResultTime)

print("-------------------------------Inexact top k result-index elimination--------------------")   
obj.inexact_query_index_elimination("soviet rainfall president grand crystal", 3,showResultTime)

print("-------------------------------Inexact top k result-champion result ---------------------")
obj.inexact_query_champion("soviet rainfall president grand crystal", 3,showResultTime)

print("-----------------------------PRINTING DOC LIST-------------------------------------------")
obj.print_dict()
obj.print_doc_list()





-----------------------------BUILDING INDEX---------------------------------------------
Retrieved in 5.03387188911438 sec.
-----------------------------Exact Top K query Result-----------------------------------
exact query result:
Doc id: 366
Doc id: 187
Doc id: 298
Doc id: 67
Time it is taking is for exact top k 0.0 sec.
-------------------------------Inexact top k result-index elimination--------------------
Index Elimination top k:
Doc id: 187
Doc id: 67
Doc id: 26
Doc id: 1
Time it is taking for index elimination is 0.0 sec.
-------------------------------Inexact top k result-champion result ---------------------
top k from champion list:
Doc id: 273
Doc id: 3
Doc id: 20
Doc id: 26
Time it is taking for champion list is 0.5060596466064453 sec.
-----------------------------PRINTING DOC LIST-------------------------------------------
indexes: 
{'!': [0.793831454668806, {2: [1.3010299956639813, [91, 135]], 3: [1.0, [413]], 4: [1.3010299956639813, [5, 268]], 12: [1.0, [2]], 17: [1.30